<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Training-AI-Agents" data-toc-modified-id="Training-AI-Agents-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Training AI Agents</a></span><ul class="toc-item"><li><ul class="toc-item"><li><span><a href="#Imports" data-toc-modified-id="Imports-1.0.1"><span class="toc-item-num">1.0.1&nbsp;&nbsp;</span>Imports</a></span><ul class="toc-item"><li><span><a href="#Stable-Baselines-Imports" data-toc-modified-id="Stable-Baselines-Imports-1.0.1.1"><span class="toc-item-num">1.0.1.1&nbsp;&nbsp;</span>Stable Baselines Imports</a></span></li></ul></li><li><span><a href="#Creating-the-Player-Class" data-toc-modified-id="Creating-the-Player-Class-1.0.2"><span class="toc-item-num">1.0.2&nbsp;&nbsp;</span>Creating the Player Class</a></span></li><li><span><a href="#Creating-a-custom-Environment" data-toc-modified-id="Creating-a-custom-Environment-1.0.3"><span class="toc-item-num">1.0.3&nbsp;&nbsp;</span>Creating a custom Environment</a></span></li><li><span><a href="#Checking-the-environment" data-toc-modified-id="Checking-the-environment-1.0.4"><span class="toc-item-num">1.0.4&nbsp;&nbsp;</span>Checking the environment</a></span></li><li><span><a href="#Random-Agent-Decisions" data-toc-modified-id="Random-Agent-Decisions-1.0.5"><span class="toc-item-num">1.0.5&nbsp;&nbsp;</span>Random Agent Decisions</a></span><ul class="toc-item"><li><span><a href="#Analysis:" data-toc-modified-id="Analysis:-1.0.5.1"><span class="toc-item-num">1.0.5.1&nbsp;&nbsp;</span>Analysis:</a></span></li></ul></li><li><span><a href="#PPO---Promixal-Policy-Optimization" data-toc-modified-id="PPO---Promixal-Policy-Optimization-1.0.6"><span class="toc-item-num">1.0.6&nbsp;&nbsp;</span>PPO - Promixal Policy Optimization</a></span><ul class="toc-item"><li><span><a href="#Analysis:" data-toc-modified-id="Analysis:-1.0.6.1"><span class="toc-item-num">1.0.6.1&nbsp;&nbsp;</span>Analysis:</a></span></li></ul></li><li><span><a href="#PPO2---Promixal-Policy-Optimization" data-toc-modified-id="PPO2---Promixal-Policy-Optimization-1.0.7"><span class="toc-item-num">1.0.7&nbsp;&nbsp;</span>PPO2 - Promixal Policy Optimization</a></span><ul class="toc-item"><li><span><a href="#Analysis:" data-toc-modified-id="Analysis:-1.0.7.1"><span class="toc-item-num">1.0.7.1&nbsp;&nbsp;</span>Analysis:</a></span></li></ul></li><li><span><a href="#A2C---Advantage-Actor-Critic" data-toc-modified-id="A2C---Advantage-Actor-Critic-1.0.8"><span class="toc-item-num">1.0.8&nbsp;&nbsp;</span>A2C - Advantage Actor Critic</a></span><ul class="toc-item"><li><span><a href="#Analysis:" data-toc-modified-id="Analysis:-1.0.8.1"><span class="toc-item-num">1.0.8.1&nbsp;&nbsp;</span>Analysis:</a></span></li></ul></li></ul></li></ul></li></ul></div>

# Training AI Agents

### Imports

I am using Stable Baselines, and Open AI's gym to create and test the environment. I am also brining in player.py, that will provide the probabilities of an action happening, which are determined from NBA player statistics from the current NBA season.

In [209]:
#Lots of help from Dustin Pierce at General Assembly
#https://stable-baselines.readthedocs.io/en/master/guide/custom_env.html
#https://github.com/koulanurag/ma-gym/blob/master/ma_gym/envs/pong_duel/pong_duel.py
#https://github.com/hardmaru/slimevolleygym/blob/master/slimevolleygym/slimevolley.py
#https://medium.com/@m.alzantot/you-can-see-what-is-the-observation-space-by-print-env-observation-space-c4e59e64ac52

import copy
import logging

import gym
import numpy as np
from gym import spaces
from gym.utils import seeding

logger = logging.getLogger(__name__)

import random
import time
# import ball  --potential future add on
# from player import Player

from ..utils.draw import draw_grid, fill_cell, draw_circle, write_cell_text, draw_score_board

#### Stable Baselines Imports

In [518]:
from stable_baselines.common.env_checker import check_env

from stable_baselines.common.policies import MlpPolicy
from stable_baselines.common import make_vec_env
from stable_baselines import PPO1, A2C, PPO2, results_plotter

ModuleNotFoundError: No module named 'tensorflow.contrib'

### Creating the Player Class

In [523]:
class Player():
    
    def __init__(self, player_name, _has_ball=False):

        self.player_name = player_name
        self._is_defended = False
        self._has_ball = True
        self._close_range = False
        self._midrange = False
        self._three_point_range = True


        self.shooting_close = np.random.beta(df[df['PLAYER_NAME' == player_name]])
        self.shooing_midrange = random.randint(40, 60)/100
        self.shooting3pts = random.randint(30, 45)/100        

In [524]:
class PlayerD():

    def __init__(self, player_name):
        
        self.player_name = player_name
        self._is_defended = False
        self._has_ball = False
        self._close_range = False
        self._midrange = False
        self._three_point_range = True

        self.steal = random.randint(0, 3)/100
        self.block = random.randint(0, 4)/100

### Creating a custom Environment

In [525]:
class BasketballEnv(gym.Env):
    """
    Custom Environment that follows gym interface.
    This is a simple env where multiple agents learn strategies to put the ball in the hoop.
    For this simple iteration, actions will be determined by probabilities rather than physics.
    """
    # In google colab, we cannot implement the GUI ('human' render mode)
    metadata = {'render.modes': ['human', 'rgb_array']}

    
    def __init__(self, step_cost=0.0, reward=0, max_rounds=1):
        #Grid size will be standard basketball halfcourt at 6"=1'-0" scale
        self._grid_shape = (100, 94)

        #Number of players
        self.n_agents = 4
        self.n_teams = 2
        self.n_agents_team_A = int(self.n_agents / 2)
        self.n_agents_team_B = int(self.n_agents / 2)
        self.reward = reward
        self._max_rounds = max_rounds
        self.action_space = spaces.MultiDiscrete([9, 2, 2])
        self.player_w_ball=[True, False]

        self._step_count = 0
        self._step_cost = step_cost
        self._total_episode_reward = [0 for _ in range(self.n_teams)]
        self.agent_pos = {0: (self._grid_shape[0]//2, self._grid_shape[1] - 2),
                         1: (self._grid_shape[0]//5, self._grid_shape[1] - 2),
                         2: (self._grid_shape[0]//2, self._grid_shape[1] - 8),
                         3: (self._grid_shape[0]//5, self._grid_shape[1] - 8)}
        self.x = [env.agent_pos[x][0] for x in range(0,4)]
        self.y = [env.agent_pos[y][1] for y in range(0,4)]
        self.t = 24

        self._agent_dones = None
        self.__rounds = 0

        # Observing agent positions for 4 agents
        self._obs_low = np.array([0., 0., 0., 0., 0., 0., 0., 0.])
        self._obs_high = np.array([1., 1., 1., 1., 1., 1., 1., 1,])
        self.observation_space = spaces.Box(low=self._obs_low, high=self._obs_high,
                                        dtype=np.float32)

        self.viewer = None
        self.seed()
        
    def is_done(self):
        if self.__rounds == self._max_rounds:
            return True
        else:
            return False
        
    def get_action_meanings(self, agent_i=None):
        if agent_i is not None:
            assert agent_i <= self.n_agents
            return [ACTION_MEANING[i] for i in range(self.action_space[agent_i].n)]
        else:
            return [[ACTION_MEANING[i] for i in range(ac.n)] for ac in self.action_space]

    def __create_grid(self):
        _grid = [[PRE_IDS['empty'] for _ in range(self._grid_shape[1])] for row in range(self._grid_shape[0])]
        return _grid

    def __update_agent_view(self, agent_i):
        for row in range(self.agent_prev_pos[agent_i][0],
                         self.agent_prev_pos[agent_i][0]):
            self._full_obs[row][self.agent_prev_pos[agent_i][1]] = PRE_IDS['empty']

        for row in range(self.agent_pos[agent_i][0], self.agent_pos[agent_i][0]):
            self._full_obs[row][self.agent_pos[agent_i][1]] = PRE_IDS['agent'] + str(agent_i + 1) \
                                                              + '_' + str(row - self.agent_pos[agent_i][0])

#     def __draw_base_img(self):
#         self._base_img = draw.draw_grid(self._grid_shape[0], self._grid_shape[1],
#                                    cell_size=CELL_SIZE, fill='white', line_color='white')

    def __init_full_obs(self):
        self._full_obs = self.__create_grid()
        for agent_i in range(self.n_agents):
            self.__update_agent_view(agent_i)

        for agent_i in range(self.n_agents):
            self.__update_agent_view(agent_i)

#         self.__draw_base_img()

    #Countdown timer as 24 second shot clock for each round
    #https://www.geeksforgeeks.org/how-to-create-a-countdown-timer-using-python/
    def countdown(self, t=24):     
        while t: 
            mins, secs = divmod(t, 60) 
            timer = '{:02d}:{:02d}'.format(mins, secs)  
            time.sleep(1) 
            t -= 1
            self.t = t
    
    def __init_countdown(self, t):
        return self.countdown(t)
        

    def get_agent_obs(self):
        _obs = []

        for agent_i in range(self.n_agents):
            pos = self.agent_pos[agent_i]
            _agent_i_obs_a = pos[0] / self._grid_shape[0]
            _agent_i_obs_b = pos[1] / self._grid_shape[1]
            
            _obs.append(_agent_i_obs_a)
            _obs.append(_agent_i_obs_b)

        return np.array(_obs)
    
##############
#Define Reset#   
##############

    def reset(self):
        self.__rounds = 0
        self.__init_countdown(24)
        
        #Set starting positions for agents in Team A
        self.agent_pos[0] = (self._grid_shape[0]//2, self._grid_shape[1] - 2)
        self.agent_pos[1] = (self._grid_shape[0]//5, self._grid_shape[1] - 2)

        
        #Set starting positions for agents in Team B
        self.agent_pos[2] = (self._grid_shape[0]//2, self._grid_shape[1] - 8)
        self.agent_pos[3] = (self._grid_shape[0]//5, self._grid_shape[1] - 8)

        
        self.agent_prev_pos = {_: self.agent_pos[_] for _ in range(self.n_agents)}
        self._agent_dones = False
        self.__init_full_obs()
        self._step_count = 0
        self._total_episode_reward = [0 for _ in range(self.n_teams)]

        return self.get_agent_obs()

    
###############################
#Define Properties and Actions#   
###############################
    
            
    #This will determine success of an action
    def action_success(self, p_1):
        return np.random.choice([0, 1], p=[1 - p_1, p_1])

    #Determine if a player is close to the goal
    def close_range(self):
        for agent_i in range(n_agents):
            if self.y > 0 and self.y < self._grid_shape[1] and self.x > 0 and self.x < self._grid_shape[0]:
                if np.sqrt((x.self - GOAL[0])**2 + (y.self-GOAL[1])**2) <= 6:
                    agent_i.player._close_range = True

    #Determine if a player is mid-range from the goal
    def midrange(self):
        for agent_i in range(n_agents):
            if self.y > 0 and self.y < self._grid_shape[1] and self.x > 0 and self.x < self._grid_shape[0]:
                if player._close_range == False and player._three_point_range == False:
                    agent_i.player._midrange = True

    #Determine if a player is in three point range
    def _three_point_range(self):
        for agent_i in range(n_agents):
            if self.y > 0 and self.y < self._grid_shape[1] and self.x > 0 and self.x < self._grid_shape[0]:
                if self.y <= 19.67 and self.x <= 6.67 or self.x >= 93.33:
                    player._three_point_range = True
                elif self.y > 19.67 and np.sqrt((x.self - GOAL[0])**2 + (y.self-GOAL[1])**2) > 44.3:
                    agent_i.player._three_point_range = True

    #define defensive rebound, will be a reward for the defensive team
    def d_rebound(self):
        return True
        
    def rebound(self):
        for agent_i in range(self.n_agents_team_A):
            if self.action_success(0.3):
                #UPDATE THE PLAYER_W_BALL:
#                 o_rebounder = random.choice([[True, False], [False, True]])
#                 self.player_w_ball = o_rebounder
#                 self.__init_countdown(14)
#                 if o_rebounder == [True, False]:
#                     player._has_ball = True
#                     player2._has_ball = False
#                 else:
#                     player._has_ball = False
#                     player2._has_ball = True
                return 0.2
            else:
                return self.d_rebound()

    #define shot, a made shot will be a reward for the offensive team
    def shot(self):
        
        for agent_i in range(self.n_agents_team_A):

            #Can only shoot if the player has the ball -- [1,0]
            if player._has_ball:

                #Close range shot
                if player._close_range:
                    shot = self.action_success(player.shooting_close)
                    if shot == 1:
                        return 2
                    else:
                        return self.rebound()

                #Midrange shot
                if player._midrange:
                    shot = self.action_success(player.shooting_midrange)
                    if shot == 1:
                        return 2
                    else:
                        return self.rebound()

                #3 point shot
                if player._three_point_range:
                    shot = self.action_success(player.shooting3pts)
                    if shot == 1:
                        return 3
                    else:
                        return self.rebound()
                    
            #Can only shoot if the player has the ball -- [0,1]
            if player2._has_ball:

                #Close range shot
                if player2._close_range:
                    shot = self.action_success(player2.shooting_close)
                    if shot == 1:
                        return 2
                    else:
                        return self.rebound()

                #Midrange shot
                if player2._midrange:
                    shot = self.action_success(player2.shooting_midrange)
                    if shot == 1:
                        return 2
                    else:
                        return self.rebound()

                #3 point shot
                if player2._three_point_range:
                    shot = self.action_success(player2.shooting3pts)
                    if shot == 1:
                        return 3
                    else:
                        return self.rebound()
                        
    def ball_pass(self):
        for agent_i in range(n_agents_team_A):
            if player._has_ball == True:
                player._has_ball = False
                player2._has_ball = True
                self.player_w_ball = [0,1]
                
            if player2._has_ball == True:
                player._has_ball = True
                player2._has_ball = False
                self.player_w_ball = [1,0]
                
            

    def defended(self):
        for agent_i in range(n_agents_team_B):
            for agent_j in n_agents_team_A:
                if np.sqrt(agent_i.self.x**2 + agent_i.self.y**2) < 5:
                    agent_j.player._is_defended=True
                else:
                    agent_j.player._is_defended=False
    
    def steal(self):
        for agent_i in range(self.n_agents_team_B):
            for agent_j in range(self.n_agents_team_A):
                if player._has_ball and player._is_defended:
                    return action_success(0.02)
    
    def block(self):
        for agent_i in range(self.n_agents_team_B):
            for agent_j in range(self.n_agents_team_A):
                if player._has_ball and player._is_defended and player._close_range:
                    return action_success(0.04)
                if player._has_ball and player._is_defended and player._midrange:
                    return action_success(0.03)
                if player._has_ball and player._is_defended and player._three_point_range:
                    return action_success(0.02)
                
    def out_of_bounds(self):
        for agent_x in range(self.n_agents):
            if self.x[agent_x] > 0 and self.x[agent_x] < self._grid_shape[0] and self.y[agent_x] > 0 and self.y[agent_x] < self._grid_shape[1]:
                return False
            else:
                return True

    def is_valid(self, pos):
        return (0 <= pos[0] < self._grid_shape[0]) and (0 <= pos[1] < self._grid_shape[1])

    def _is_cell_vacant(self, pos):
        return self.is_valid(pos) and (self._full_obs[pos[0]][pos[1]] == PRE_IDS['empty'])

    
    
###############
#Define Render#   
###############

    def render(self, mode='human'):
        img = copy.copy(self._base_img)
        for agent_i in range(self.n_agents):
            for row in self.agent_pos[agent_i][0]:
                fill_cell(img, (row, self.agent_pos[agent_i][1]), cell_size=CELL_SIZE, fill=AGENT_COLORS[agent_i])

        img = draw_border(img, border_width=2, fill='gray')

        img = np.asarray(img)
        if mode == 'rgb_array':
            return img
        elif mode == 'human':
            from gym.envs.classic_control import rendering
            if self.viewer is None:
                self.viewer = rendering.SimpleImageViewer()
            self.viewer.imshow(img)
            return self.viewer.isopen

    def __update_agent_pos(self, agent_i, move):

        curr_pos = copy.copy(self.agent_pos[agent_i])
        for agent_i in range(self.n_agents):
            if self.out_of_bounds() == False:
                if move == 0:  # noop
                    next_pos = None
                elif move == 1:  # up
                    next_pos = [curr_pos[0] - 1, curr_pos[1]]
                elif move == 2:  # upright
                    next_pos = [curr_pos[0] - 1, curr_pos[1] + 1]
                elif move == 3:  # right
                    next_pos = [curr_pos[0], curr_pos[1] + 1]
                elif move == 4:  # downright
                    next_pos = [curr_pos[0] + 1, curr_pos[1] + 1]
                elif move == 5:  # down
                    next_pos = [curr_pos[0] + 1, curr_pos[1]]
                elif move == 6:  # downleft
                    next_pos = [curr_pos[0] + 1, curr_pos[1] - 1]
                elif move == 7:  # left
                    next_pos = [curr_pos[0], curr_pos[1] - 1]
                elif move == 8:  # upleft
                    next_pos = [curr_pos[0] - 1, curr_pos[1] - 1]
#                 else:
#                     raise Exception('Action Not found!')


                    if next_pos is not None:
                        self.agent_prev_pos[agent_i] = self.agent_pos[agent_i]
                        self.agent_pos[agent_i] = next_pos
                        self.__update_agent_view(agent_i)
            

#############
#Define Seed#   
#############

    def seed(self, n=None):
        self.np_random, seed = seeding.np_random(n)
        return [seed]

#############
#Define Step#   
#############
    
    def step(self, action_n=[0,0,0,0]):
#         assert len(action_n) == self.n_agents
        self._step_count += 1
        rewards = [self._step_cost for _ in range(self.n_teams)]

        # if shot made, new round
        if self.shot() == 2:
            rewards = [2, 0]
            self.__rounds += 1
            
        elif self.shot() == 3:
            rewards = [3, 0]
            self.__rounds += 1
            
        elif self.shot() == 1:
            rewards = [0, 1]
            self.__rounds += 1
            
        elif self.shot() == 0.2:
            rewards = [0.2, 0]
            self.__rounds += 1

        # if steal made, new round
        if self.steal():
            rewards = [0, 2]
            self.__rounds += 1
        
        # if block made, new round
        if self.block():
            rewards = [0, 2]
            self.__rounds += 1
            
        # if Offense fails to get off a shot within time limit, new round
        if self.t < 1:
            rewards = [0, 2]
            self.__rounds += 1
            
        if self.out_of_bounds():
            rewards = [-10, -10]
            self.__rounds +=1
                        
        if self.__rounds == self._max_rounds:
            self._agent_dones = True
            
        elif self.t < 1:
            self._agent_dones = True
            self.__rounds +=1
            
        else:
            for agent_i in range(self.n_agents_team_A):
                self.__update_agent_pos(agent_i, action_n[agent_i])
            for agent_j in range(self.n_agents_team_B):
                self.__update_agent_pos(agent_j, action_n[agent_j])
                
        for i in range(self.n_teams):
            self._total_episode_reward[i] += rewards[i]

        return self.get_agent_obs(), rewards[0]-rewards[1], self._agent_dones, {'rounds': self.__rounds}
    
    def close(self):
        if self.viewer is not None:
            self.viewer.close()
            self.viewer = None

# Define constants for clearer code

CELL_SIZE = 5

#Goal Location
GOAL = [50, 10.5]

ACTION_MEANING_TEAM_A = {
    0 : 'NOOP',
    1 : 'UP',
    2 : 'UPRIGHT',
    3 : 'RIGHT',
    4 : 'DOWNRIGHT',
    5 : 'DOWN',
    6 : 'DOWNLEFT',
    7 : 'LEFT',
    8 : 'UPLEFT',
    9 : 'BALL_PASS',
    10 : 'SHOOT',
}

ACTION_MEANING_TEAM_B = {
    0 : 'NOOP',
    1 : 'UP',
    2 : 'UPRIGHT',
    3 : 'RIGHT',
    4 : 'DOWNRIGHT',
    5 : 'DOWN',
    6 : 'DOWNLEFT',
    7 : 'LEFT',
    8 : 'UPLEFT',
    11 : 'STEAL',
    12 : 'BLOCK',
}

AGENT_TEAMS = {
    0: 'A',
    1: 'A',
    2: 'B',
    3: 'B',
}

AGENT_COLORS = {
    0: 'red',
    1: 'red',
    2: 'blue',
    3: 'blue',
}

WALL_COLOR = 'black'

# each pre-id should be unique and single char
PRE_IDS = {
    'agent': 'A',
    'goal' : 'G',
    'empty': 'O'
}


### Checking the environment

In [526]:
env = BasketballEnv()
# It will check your custom environment and output additional warnings if needed
check_env(env)

C:\Users\kendr\anaconda3\lib\site-packages\gym\logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


### Random Agent Decisions

In [503]:
agent.total_reward

[0, 0]

In [509]:
class RandomAgentA:
    def __init__(self, player1, player2):
        self.total_reward = [0,0]
        player = Player(player1, _has_ball=True)
        player2 = Player2(player2)

    def step(self, env):
        # current_obs = env.get_observation()
        actions = ACTION_MEANING_TEAM_A
        action = random.choice(actions)
        reward = env.step(action)
        print(f"Took action {action} and got reward {reward}")
        self.total_reward += reward

In [509]:
class RandomAgentB:
    def __init__(self, player1, player2):
        self.total_reward = [0,0]
        playerd = PlayerD(player1)
        playerd2 = PlayerD(player2)

    def step(self, env):
        # current_obs = env.get_observation()
        actions = ACTION_MEANING_TEAM_B
        action = random.choice(actions)
        reward = env.step(action)
        print(f"Took action {action} and got reward {reward}")
        self.total_reward += reward

In [510]:
env = BasketballEnv()
agentA0 = RandomAgentA('Luka Doncic')
agentA1 = RandomAgentA('Kristaps Porzingis')
agentB2 = RandomAgentB('Julius Randle')
agentB2 = RandomAgentB('RJ Barrett')



while not env.is_done():
    agent.step(env)
print(f"Total reward: {agent.total_reward}")

Took action DOWN and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 2})
Took action LEFT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), 0.0, None, {'rounds': 2})
Took action NOOP and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 4})
Took action DOWN and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 5})
Took action DOWN and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 7})
Took action RIGHT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1,

Took action UPLEFT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), 0.2, None, {'rounds': 246})
Took action DOWNRIGHT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 248})
Took action DOWNRIGHT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 250})
Took action SHOOT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 253})
Took action UP and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), 0.0, None, {'rounds': 253})
Took action SHOOT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2    

       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 485})
Took action RIGHT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 487})
Took action UPLEFT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 489})
Took action LEFT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 492})
Took action NOOP and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 495})
Took action UP and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 497})
Took action NOOP and got reward (array([0.5       , 0.9787234 , 0.2

       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 714})
Took action BALL_PASS and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 716})
Took action BALL_PASS and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 717})
Took action UPRIGHT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), 0.0, None, {'rounds': 717})
Took action UP and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), 3, None, {'rounds': 718})
Took action DOWN and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 721})
Took action STEAL and got reward (array([0.5       , 0.97

       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 958})
Took action DOWN and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 960})
Took action LEFT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 961})
Took action RIGHT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 963})
Took action DOWNLEFT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 965})
Took action DOWNRIGHT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 967})
Took action BLOCK and got reward (array([0.5       , 0.978

...

       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40021})
Took action UPLEFT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), 3, None, {'rounds': 40022})
Took action STEAL and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40024})
Took action NOOP and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40026})
Took action DOWN and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40028})
Took action UPRIGHT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40029})
Took action DOWNRIGHT and got reward (array([0.5   

       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40251})
Took action SHOOT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), 0.0, None, {'rounds': 40251})
Took action LEFT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40252})
Took action LEFT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40255})
Took action BALL_PASS and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40256})
Took action UPLEFT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40257})
Took action STEAL and got reward (array([0.5   

       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40452})
Took action DOWNRIGHT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), 0.0, None, {'rounds': 40452})
Took action BLOCK and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40454})
Took action UPRIGHT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40455})
Took action BALL_PASS and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40456})
Took action UPLEFT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40457})
Took action RIGHT and got reward (array

       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40694})
Took action NOOP and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40695})
Took action DOWN and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40697})
Took action DOWN and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40698})
Took action UPLEFT and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40700})
Took action UP and got reward (array([0.5       , 0.9787234 , 0.2       , 0.9787234 , 0.5       ,
       0.91489362, 0.2       , 0.91489362]), -1, None, {'rounds': 40702})
Took action UP and got reward (array([0.5       , 0.9787

KeyboardInterrupt: 

In [497]:
env.is_done()

In [ ]:
print(env.get_agent_obs(), env.agent_pos)

#### Analysis:
Analysis of the random agent results go here.

### PPO - Promixal Policy Optimization

In [ ]:
env = gym.make('BasketballEnv')

model = PPO1(MlpPolicy, env, verbose=1)
model.learn(total_timesteps=25000)
model.save("ppo1_Basketball")

# model = PPO1.load("ppo1_cartpole")

obs = env.reset()
while True:
    action, _states = model.predict(obs)
    obs, rewards, dones, info = env.step(action)
    env.render()

In [ ]:
stable_baselines.plot_results()

#### Analysis:
Analysis of the PPO Model results go here.

### PPO2 - Promixal Policy Optimization

In [ ]:
# multiprocess environment
env = make_vec_env('BasketballEnv', n_envs=4)

model = PPO2(MlpPolicy, env, verbose=1)
model.learn(total_timesteps=25000)
model.save("ppo2_basketball")

del model # remove to demonstrate saving and loading

model = PPO2.load("ppo2_basketball")

# Enjoy trained agent
obs = env.reset()
while True:
    action, _states = model.predict(obs)
    obs, rewards, dones, info = env.step(action)
    env.render()

In [ ]:
stable_baselines.plot_results()

#### Analysis:
Analysis of the PPO2 Model results go here.

### A2C - Advantage Actor Critic

In [ ]:
# https://stable-baselines.readthedocs.io/en/master/modules/a2c.html
# Parallel environments
env = make_vec_env('BasketballEnv', n_envs=4)

model = A2C(MlpPolicy, env, verbose=1)
model.learn(total_timesteps=25000)
model.save("a2c_basketball")

del model # remove to demonstrate saving and loading

model = A2C.load("a2c_cartpole")

obs = env.reset()
while True:
    action, _states = model.predict(obs)
    obs, rewards, dones, info = env.step(action)
    env.render()

In [ ]:
stable_baselines.plot_results()

#### Analysis:
Analysis of the A2C Model results go here.